In [1]:
using FileIO;
using LibSndFile;
using Plots;
using DSP;
using SampledSignals;
using FixedPointNumbers;
using CUDA

In [2]:
tetris = load("tetris_piano_mono.wav");
fs = round(Int,tetris.samplerate);
tetris.data = tetris.data[1:(10*fs),:];
original = Float32.(tetris.data[:,1] .+ tetris.data[:,2]);
tetris

441000-frame, 2-channel SampleBuf{Q0f15, 2}
10.0s sampled at 44100.0Hz
▁▁▅▅▄▄▃▆▅▆▆▆▆▅▆▆▆▆▆▆▅▆▆▅▅▅▆▆▆▆▅▆▅▄▃▆▆▅▆▆▆▆▅▅▅▅▄▆▆▅▆▅▅▅▅▆▅▄▃▆▆▅▅▅▆▆▅▅▅▆▆▅▅▅▅▄▄▃▃▂
▁▁▆▆▅▄▄▆▅▆▅▆▅▅▆▆▆▅▅▅▅▆▅▅▄▄▆▅▆▅▅▆▅▅▄▆▅▅▆▅▅▅▅▄▄▄▄▅▅▅▆▅▅▄▆▆▅▅▄▆▅▅▅▄▆▅▅▅▄▆▅▅▄▄▄▄▄▃▃▃

Analysis Filter Bank

In [3]:
LA = FIRFilter([0.25,0.5,0.25],1//2);
HA = FIRFilter([-0.125,-0.25,0.75,-0.25,-0.125],1//2);
LS = FIRFilter([-0.25,0.5,1.5,0.5,-0.25],2//1);
HS = FIRFilter([-0.5,1,-0.5],2//1);

In [12]:
x = [original];
for octave ∈ 1:3
    y = copy(x);
    append!(y,[[]]);
    y[end-1] = filt(HA, x[end]);
    y[end] = filt(LA, x[end]);
    x = y;
end

In [13]:
size.(x)

4-element Vector{Tuple{Int64}}:
 (220500,)
 (110250,)
 (55125,)
 (55125,)

Synthesis Filter Bank

In [9]:
for octave ∈ 1:3    
    y = copy(x[1:end-1]);
    y[end] = filt(LS, x[end]) .+ filt(HS, x[end-1]);
    x = y
end

In [10]:
R = Q0f15.(x[1]);

In [11]:
recovered = copy(tetris);
recovered.data = hcat(R,R);
recovered

441000-frame, 2-channel SampleBuf{Q0f15, 2}
10.0s sampled at 44100.0Hz
▁▁▆▆▅▅▄▆▆▆▆▇▆▆▇▆▇▆▆▆▆▆▆▆▆▅▆▆▇▆▆▇▆▅▅▆▆▆▆▆▆▆▆▆▅▅▅▆▆▆▇▆▆▅▆▇▆▅▄▆▆▆▆▅▆▆▆▆▅▆▆▆▆▅▅▅▄▄▄▃
▁▁▆▆▅▅▄▆▆▆▆▇▆▆▇▆▇▆▆▆▆▆▆▆▆▅▆▆▇▆▆▇▆▅▅▆▆▆▆▆▆▆▆▆▅▅▅▆▆▆▇▆▆▅▆▇▆▅▄▆▆▆▆▅▆▆▆▆▅▆▆▆▆▅▅▅▄▄▄▃